* Inicialmente trabalhar com o dataset inteiro e utilizar as diferentes extrações de features
* Depois ir pelo segundo caminho

# Importando Libs

In [1]:
# Libs matplotlib, numpy and pandas
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd

# Lib librosa
import librosa
import librosa.display

# Lib OS
from os import listdir
from os.path import isfile, join, exists

# Lib ipwidgets
from ipywidgets import interact, IntSlider, interact_manual

# Lib IPtyhon Display
import IPython.display as ipd

# Lib glob
import glob

# Lib sklearn
from sklearn import svm

# Carregando Dataset

* Baixar todo o dataset (https://www.kaggle.com/carlthome/gtzan-genre-collection)

In [2]:
def import_signal(path):
    
    # Test if path exists
    if( exists(path) == False ):
        print("Path does not exist, download from https://www.kaggle.com/carlthome/gtzan-genre-collection")
        return 0, 0
    
    # Load files woth glob
    files = glob.glob(path + '*.au')
    audios = []
    
    # Load audio files with sample rate 22050 Hz
    for file in files: 
        s, sr = librosa.core.load(file, sr=22050)
        audios.append(s)
        
    # Return audio vector and sample rate
    return audios, sr

## Popular (0)

In [3]:
# Import Popular audio files
pop_audios, pop_sr = import_signal('genres/pop/')

pop_audios_df = pd.DataFrame([[x] for x in pop_audios], columns=['x'])
pop_audios_df['y'] = 0
pop_audios_df['y2'] = 0
#pop_audios_df.head()

In [4]:
@interact(x=IntSlider(min=0, max=99, step=1, value=0))
def _f(x):
    ipd.Audio(pop_audios[x], rate=pop_sr)
    
x = 54
ipd.Audio(pop_audios[x], rate=pop_sr)

interactive(children=(IntSlider(value=0, description='x', max=99), Output()), _dom_classes=('widget-interact',…

## Classic (1)

In [5]:
# Import Classical audio files
classical_audios, classical_sr = import_signal('genres/classical/')

classical_audios_df = pd.DataFrame([[x] for x in classical_audios], columns=['x'])
classical_audios_df['y'] = 1
classical_audios_df['y2'] = 0
#classical_audios_df.head()

In [6]:
@interact(x=IntSlider(min=0, max=99, step=1, value=0))
def _f(x):
    ipd.Audio(classical_audios[x], rate=classical_sr)
    
x = 54
ipd.Audio(classical_audios[x], rate=classical_sr)

interactive(children=(IntSlider(value=0, description='x', max=99), Output()), _dom_classes=('widget-interact',…

## Jazz (2)

In [7]:
# Import Jazz audio files
jazz_audios, jazz_sr = import_signal('genres/jazz/')

jazz_audios_df = pd.DataFrame([[x] for x in jazz_audios], columns=['x'])
jazz_audios_df['y'] = 2
jazz_audios_df['y2'] = 1
#jazz_audios_df.head()

In [8]:
@interact(x=IntSlider(min=0, max=99, step=1, value=0))
def _f(x):
    ipd.Audio(jazz_audios[x], rate=jazz_sr)
    
x = 54
ipd.Audio(jazz_audios[x], rate=jazz_sr)

interactive(children=(IntSlider(value=0, description='x', max=99), Output()), _dom_classes=('widget-interact',…

## Rock (3)

In [9]:
# Import Rock audio files
rock_audios, rock_sr = import_signal('genres/rock/')

rock_audios_df = pd.DataFrame([[x] for x in rock_audios], columns=['x'])
rock_audios_df['y'] = 3
rock_audios_df['y2'] = 1
#rock_audios_df.head()

In [10]:
@interact(x=IntSlider(min=0, max=99, step=1, value=0))
def _f(x):
    ipd.Audio(rock_audios[x], rate=rock_sr)
    
x = 54
ipd.Audio(rock_audios[x], rate=rock_sr)

interactive(children=(IntSlider(value=0, description='x', max=99), Output()), _dom_classes=('widget-interact',…

## Verificando os Sample Rates

In [11]:
pop_sr == classical_sr == jazz_sr == rock_sr

True

In [12]:
sr = pop_sr
sr

22050

## Criando vertor de audios

In [13]:
audios = (
    pd.concat([ pop_audios_df, 
                classical_audios_df, 
                jazz_audios_df, 
                rock_audios_df])
    .sample(frac=1)
    .reset_index(drop=True) #shuffle
)

print(f'Rows: {len(audios)}')
#audios.head()

Rows: 400


## Dividindo entre  Train e Test

In [14]:
# Splitting int train and test
msk = np.random.rand(len(audios)) < 0.8
train = audios[msk]
test = audios[~msk]

print(f'Rows train:{len(train)}')
print(f'Rows test:{len(test)}')

Rows train:315
Rows test:85


In [15]:
print("Train count Y axis:")
print(train.groupby('y').count())
print(" ")
print("Train count Y2 axis:")
print(train.groupby('y2').count())
print(" ")
print("Test count Y axis:")
print(test.groupby('y').count())
print(" ")
print("Test count Y2 axis:")
print(test.groupby('y2').count())

Train count Y axis:
    x  y2
y        
0  74  74
1  82  82
2  76  76
3  83  83
 
Train count Y2 axis:
      x    y
y2          
0   156  156
1   159  159
 
Test count Y axis:
    x  y2
y        
0  26  26
1  18  18
2  24  24
3  17  17
 
Test count Y2 axis:
     x   y
y2        
0   44  44
1   41  41


# Feature extraction

## MFCC

In [ ]:
mfcc_list_train = []

for x in train['x']:
      
    mfcc = np.array(librosa.feature.mfcc(y=x, sr=sr)).flatten()
    zeros = np.zeros((26280 - len(mfcc)))
    mfcc_list_train.append(np.concatenate((mfcc, zeros), axis=0))
    
train['mfcc'] = mfcc_list_train
train.head()

In [ ]:
mfcc_list_test = []

for x in test['x']:
    
    mfcc = np.array(librosa.feature.mfcc(y=x, sr=sr)).flatten()
    zeros = np.zeros((26280 - len(mfcc)))
    mfcc_list_test.append(np.concatenate((mfcc, zeros), axis=0))
    
test['mfcc'] = mfcc_list_test
test.head()

## LPC

In [ ]:
lpc_list = []

for x in train['x']:
    
    lpc = librosa.lpc(x, 6)
    lpc_list.append(lpc)
    
train['lpc'] = lpc_list
train.head()

In [ ]:
lpc_list = []

for x in test['x']:
    
    lpc = librosa.lpc(x, 6)
    lpc_list.append(lpc)
    
test['lpc'] = lpc_list
test.head()

# First Scenario

## Plot functions

In [ ]:
# pesquisar

## Using MFCC

In [ ]:
model_mfcc = svm.SVC()
model_mfcc.fit(train['mfcc'].to_list(), train['y'].to_list())

In [ ]:
print('Train accuracy: {:.1%}'.format(model_mfcc.score(train['mfcc'].to_list(), train['y'].to_list())))
print('Test accuracy: {:.1%}'.format(model_mfcc.score(test['mfcc'].to_list(), test['y'].to_list())))

## Using LPC

In [ ]:
model_lpc = svm.SVC()
model_lpc.fit(train['lpc'].to_list(), train['y'].to_list())

In [ ]:
print('Train accuracy: {:.1%}'.format(model_lpc.score(train['lpc'].to_list(), train['y'].to_list())))
print('Test accuracy: {:.1%}'.format(model_lpc.score(test['lpc'].to_list(), test['y'].to_list())))

## Using MFCC and LPC

# Second Scenario

In [ ]:
def second_scenario_classification(train, test, feature_ex_svm1='lpc', feature_ex_svm23='mfcc'):
    
    # SVM1
    model1 = svm.SVC()
    model1.fit(train[f'{feature_ex_svm1}'].to_list(), train['y2'].to_list())
    train['y2_predicted'] = model1.predict(train[f'{feature_ex_svm1}'].to_list())
    
    #SVM2
    train_2 = train[train['y2_predicted']==0]
    train_2 = train_2[train_2['y'].isin([0,1])]
    test_2 = test[test['y2']==0]
    model2 = svm.SVC()
    model2.fit(train_2[f'{feature_ex_svm23}'].to_list(), train_2['y'].to_list())
    
    #SVM3
    train_3 = train[train['y2_predicted']==1]
    train_3 = train_3[train_3['y'].isin([2,3])]
    test_3 = test[test['y2']==1]
    model3 = svm.SVC()
    model3.fit(train_3[f'{feature_ex_svm23}'].to_list(), train_3['y'].to_list())
    
    train_score = (
        model2.score(train_2[f'{feature_ex_svm23}'].to_list(), train_2['y'].to_list()) * 0.5 +
        model3.score(train_3[f'{feature_ex_svm23}'].to_list(), train_3['y'].to_list()) * 0.5
    )
    
    test_score = (
        model2.score(test_2[f'{feature_ex_svm23}'].to_list(), test_2['y'].to_list()) * 0.5 +
        model3.score(test_3[f'{feature_ex_svm23}'].to_list(), test_3['y'].to_list()) * 0.5
    )
    
    print('Train accuracy: {:.1%}'.format(train_score))
    print('Test accuracy: {:.1%}'.format(test_score))

In [ ]:
second_scenario_classification(train, test, feature_ex_svm1='lpc', feature_ex_svm23='mfcc')

In [ ]:
second_scenario_classification(train, test, feature_ex_svm1='lpc', feature_ex_svm23='lpc')

In [ ]:
second_scenario_classification(train, test, feature_ex_svm1='mfcc', feature_ex_svm23='mfcc')

In [ ]:
second_scenario_classification(train, test, feature_ex_svm1='mfcc', feature_ex_svm23='lpc')